<a href="https://cognitiveclass.ai"><img src = "https://ibm.box.com/shared/static/9gegpsmnsoo25ikkbl4qzlvlyjbgxs5x.png" width = 400> </a>

<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Toronto</font></h1>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

#!conda install -c conda-forge beautifulsoup4 --yes # uncomment this line if you haven't completed the Foursquare API lab
from bs4 import BeautifulSoup  # map HTML Parsing Tool

import requests # import requests

#!conda install -c conda-forge geocoder --yes
import geocoder # import geocoder

print('Libraries imported.')

Libraries imported.


## 1. Download Webpage and Extract Dataset 

Neighborhood has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood. 

Luckily, this dataset exists for free on the web. Feel free to try to find this dataset on your own, but here is the link to the dataset: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M

For your convenience, I downloaded the files and placed it on the server, so you can simply run a `wget` command and access the data. So let's go ahead and do that.

In [2]:
# specify the url
neighborhoods_page = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

In [3]:
# query the website and return the html to the variable ‘page’
html_string = requests.get(neighborhoods_page).content

In [4]:
# Parse webpage
soup = BeautifulSoup(html_string, 'html.parser')

In [5]:
#extract tables
tables = soup.find_all("table")

In [6]:
#Move first table into DataFram
table = tables[0]
tab_data = [[cell.text.rstrip('\n') for cell in row.find_all(["th","td"])]
                        for row in table.find_all("tr")]
df = pd.DataFrame(tab_data)

In [7]:
#Move first row into header
df.columns = df.iloc[0,:]
df.drop(index=0,inplace=True)

In [8]:
#Only process rows with Borough assigned
df = df.query('Borough!="Not assigned"')

In [9]:
#Print Dataframe shape
df.shape

(103, 3)

In [10]:
#Print Dataframe
df

0   Postal Code           Borough  \
3           M3A        North York   
4           M4A        North York   
5           M5A  Downtown Toronto   
6           M6A        North York   
7           M7A  Downtown Toronto   
9           M9A         Etobicoke   
10          M1B       Scarborough   
12          M3B        North York   
13          M4B         East York   
14          M5B  Downtown Toronto   
15          M6B        North York   
18          M9B         Etobicoke   
19          M1C       Scarborough   
21          M3C        North York   
22          M4C         East York   
23          M5C  Downtown Toronto   
24          M6C              York   
27          M9C         Etobicoke   
28          M1E       Scarborough   
31          M4E      East Toronto   
32          M5E  Downtown Toronto   
33          M6E              York   
37          M1G       Scarborough   
40          M4G         East York   
41          M5G  Downtown Toronto   
42          M6G  Downtown Toronto   
46          M1H       Scarborough   
47          M2H        North York   
48          M3H        North York   
49          M4H         East York   
50          M5H  Downtown Toronto   
51          M6H      West Toronto   
55          M1J       Scarborough   
56          M2J        North York   
57          M3J        North York   
58          M4J         East York   
59          M5J  Downtown Toronto   
60          M6J      West Toronto   
64          M1K       Scarborough   
65          M2K        North York   
66          M3K        North York   
67          M4K      East Toronto   
68          M5K  Downtown Toronto   
69          M6K      West Toronto   
73          M1L       Scarborough   
74          M2L        North York   
75          M3L        North York   
76          M4L      East Toronto   
77          M5L  Downtown Toronto   
78          M6L        North York   
81          M9L        North York   
82          M1M       Scarborough   
83          M2M        North York   
84          M3M        North York   
85          M4M      East Toronto   
86          M5M        North York   
87          M6M              York   
90          M9M        North York   
91          M1N       Scarborough   
92          M2N        North York   
93          M3N        North York   
94          M4N   Central Toronto   
95          M5N   Central Toronto   
96          M6N              York   
99          M9N              York   
100         M1P       Scarborough   
101         M2P        North York   
103         M4P   Central Toronto   
104         M5P   Central Toronto   
105         M6P      West Toronto   
108         M9P         Etobicoke   
109         M1R       Scarborough   
110         M2R        North York   
112         M4R   Central Toronto   
113         M5R   Central Toronto   
114         M6R      West Toronto   
115         M7R       Mississauga   
117         M9R         Etobicoke   
118         M1S       Scarborough   
121         M4S   Central Toronto   
122         M5S  Downtown Toronto   
123         M6S      West Toronto   
127         M1T       Scarborough   
130         M4T   Central Toronto   
131         M5T  Downtown Toronto   
136         M1V       Scarborough   
139         M4V   Central Toronto   
140         M5V  Downtown Toronto   
143         M8V         Etobicoke   
144         M9V         Etobicoke   
145         M1W       Scarborough   
148         M4W  Downtown Toronto   
149         M5W  Downtown Toronto   
152         M8W         Etobicoke   
153         M9W         Etobicoke   
154         M1X       Scarborough   
157         M4X  Downtown Toronto   
158         M5X  Downtown Toronto   
161         M8X         Etobicoke   
166         M4Y  Downtown Toronto   
169         M7Y      East Toronto   
170         M8Y         Etobicoke   
179         M8Z         Etobicoke   

0                                        Neighbourhood  
3                                            Parkwoods  
4                                    

## 2. Fetch Coordinates

### Define function that fetches coordinates using Geocode

In [11]:
def fetch_coordinates(row):
    # initialize your variable to None
    g_ok = False

    # loop until you get the coordinates
    while(g_ok is False):
        g = geocoder.arcgis('{}, Toronto, Ontario'.format(row['Postal Code']))
        g_ok  = g.ok
    print([g.lat,g.lng])
    return [g.lat, g.lng];

### Map fetch coordinates to Postal Code  column

In [12]:
res = df.apply(fetch_coordinates, axis=1, result_type='expand')
res.columns = ['Latitude','Longitude']
df[res.columns]= res

[43.75188000000003, -79.33035999999998]
[43.73042000000004, -79.31281999999999]
[43.655140000000074, -79.36264999999997]
[43.72321000000005, -79.45140999999995]
[43.66449000000006, -79.39301999999998]
[43.66277000000008, -79.52830999999998]
[43.81153000000006, -79.19551999999999]
[43.74929000000003, -79.36168999999995]
[43.707940000000065, -79.31159999999994]
[43.65736000000004, -79.37817999999999]
[43.70799000000005, -79.44837999999999]
[43.65279000000004, -79.55405999999994]
[43.78564000000006, -79.15870999999999]
[43.72184000000004, -79.34339999999997]
[43.68970000000007, -79.30679999999995]
[43.65143000000006, -79.37556999999998]
[43.69211000000007, -79.43035999999995]
[43.648900000000026, -79.57824999999997]
[43.765750000000025, -79.17519999999996]
[43.67703000000006, -79.29541999999998]
[43.64531000000005, -79.37367999999998]
[43.68784000000005, -79.45045999999996]
[43.768200000000036, -79.21760999999998]
[43.70909000000006, -79.36409999999995]
[43.65609000000006, -79.38492999999

## 3. Create Map and Explore Data

#### Use geopy library to get the latitude and longitude values of New York City.

In [13]:
address = 'Toronto, ON'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


#### Fetch latitude and longitude for all neighborhoods of Toronto

In [14]:
def fetch_neighbourhood_coordinates(row):
    # initialize your variable to None
    g_ok = False

    # loop until you get the coordinates
    while(g_ok is False):
        g = geocoder.arcgis('{},{}, Toronto, Ontario'.format(row['Neighbourhood'], row['Borough']))
        g_ok  = g.ok
    print([row['Neighbourhood'],g.address,g.lat,g.lng])
    return [g.lat, g.lng];

In [15]:
df['Neighbourhood'] = df['Neighbourhood'].str.split(',')

In [16]:
df = df.explode('Neighbourhood')

In [17]:
df['Neighbourhood'] = df['Neighbourhood'].str.strip()

In [18]:
res2 = df.apply(fetch_neighbourhood_coordinates, axis=1, result_type='expand')
res2.columns = ['Latitude','Longitude']
df[res2.columns]= res2

['Parkwoods', 'Parkwoods Village Dr, North York, Toronto, Ontario, M3A', 43.7588952965143, -79.32032242259716]
['Victoria Village', 'Victoria Village, North York, Toronto, Ontario', 43.73154000000005, -79.31427999999994]
['Regent Park', 'Regent Park, Toronto, Ontario', 43.660690000000045, -79.36030999999997]
['Harbourfront', 'Harbourfront Centre', 43.639230000000055, -79.38306999999998]
['Lawrence Manor', 'Lawrence Manor, North York, Toronto, Ontario', 43.72294000000005, -79.43115999999998]
['Lawrence Heights', 'Lawrence Heights, North York, Toronto, Ontario', 43.72357000000005, -79.43710999999996]
["Queen's Park", "Queen's Park, Toronto, Ontario, M5S", 43.666621747669836, -79.39326407048318]
['Ontario Provincial Government', 'Toronto, Ontario', 43.648690000000045, -79.38543999999996]
['Islington Avenue', 'Islington Ave, Etobicoke, Toronto, Ontario, M8Z', 43.634187382907214, -79.51906046653036]
['Humber Valley Village', 'Humber Valley Rd, Etobicoke, Toronto, Ontario, M8Y', 43.641466413

['Oakridge', 'Oakridge, Scarborough, Toronto, Ontario', 43.698830000000044, -79.27911999999998]
['York Mills', 'York Mills Rd, North York, Toronto, Ontario, M2L 1K7', 43.74647856389376, -79.3915972517764]
['Silver Hills', 'Silver Hills, North York, Toronto, Ontario', 43.75763000000006, -79.37118999999996]
['Downsview', 'Downsview Ave, North York, Toronto, Ontario, M3M 1E4', 43.7201966122159, -79.4998953799414]
['India Bazaar', 'India Bazaar', 43.73840000000007, -79.56523999999996]
['The Beaches West', 'The Beaches, Toronto, Ontario', 43.67413000000005, -79.29643999999996]
['Commerce Court', 'Commerce Ct, Toronto, Ontario, M5H 1H1', 43.64878998985561, -79.37951489175764]
['Victoria Hotel', 'Hotel Victoria', 43.64813000000004, -79.37777999999997]
['North Park', 'North Park, North York, Toronto, Ontario', 43.72097000000008, -79.47552999999994]
['Maple Leaf Park', 'Maple Leaf Park', 43.71675000000005, -79.49131999999997]
['Upwood Park', 'Upwood Ave, North York, Toronto, Ontario, M6L 3A5', 

['Deer Park', 'Deer Park, Toronto, Ontario', 43.67797000000007, -79.40596999999997]
['CN Tower', 'CN Tower', 43.642630000000054, -79.38714999999996]
['King and Spadina', 'King St W & Spadina Ave, Toronto, Ontario, M5V', 43.645440043716434, -79.39513995283988]
['Railway Lands', 'Toronto, Ontario', 43.648690000000045, -79.38543999999996]
['Harbourfront West', 'Toronto, Ontario', 43.648690000000045, -79.38543999999996]
['Bathurst Quay', 'Bathurst Quay, Toronto, Ontario', 43.63546000000008, -79.39810999999997]
['South Niagara', 'Niagara, Toronto, Ontario', 43.64285000000007, -79.40789999999998]
['Island airport', 'Island Airport, Toronto, Ontario, M5V', 43.632100144918965, -79.39585076724106]
['New Toronto', 'New Toronto, Etobicoke, Toronto, Ontario', 43.60143000000005, -79.50924999999995]
['Mimico South', 'Mimico Ave, Etobicoke, Toronto, Ontario, M8V 1R4', 43.61299121979061, -79.49303166611847]
['Humber Bay Shores', 'Humber Bay Shores Park', 43.62686000000008, -79.47670999999997]
['South 

In [19]:
neighborhoods = df

#### Create a map of Toronto with neighborhoods superimposed on top.

In [20]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

#### Define Foursquare Credentials

In [21]:
CLIENT_ID = 'BHCJHYC3G403LX1EZBALWW2WOC1HEHTVQQYBCSQJMOFHKMYT' # your Foursquare ID
CLIENT_SECRET = 'GPFYPFS1OFN5PWSHWVTGGBGR05ZVU0DJDN24IVOG5O3VZ2SY' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: BHCJHYC3G403LX1EZBALWW2WOC1HEHTVQQYBCSQJMOFHKMYT
CLIENT_SECRET:GPFYPFS1OFN5PWSHWVTGGBGR05ZVU0DJDN24IVOG5O3VZ2SY


### Get nearby venues for the neighborhoods

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [23]:
toronto_data=df[['Borough','Neighbourhood','Latitude','Longitude']]

In [24]:
toronto_data=toronto_data.rename(columns={'Neighbourhood':'Neighborhood'})

In [25]:
toronto_data=toronto_data.reset_index(drop=True)

In [26]:
toronto_data

0             Borough                                   Neighborhood  \
0          North York                                      Parkwoods   
1          North York                               Victoria Village   
2    Downtown Toronto                                    Regent Park   
3    Downtown Toronto                                   Harbourfront   
4          North York                                 Lawrence Manor   
5          North York                               Lawrence Heights   
6    Downtown Toronto                                   Queen's Park   
7    Downtown Toronto                  Ontario Provincial Government   
8           Etobicoke                               Islington Avenue   
9           Etobicoke                          Humber Valley Village   
10        Scarborough                                        Malvern   
11        Scarborough                                          Rouge   
12         North York                                      Don Mills   
13          East York                                  Parkview Hill   
14          East York                               Woodbine Gardens   
15   Downtown Toronto                                Garden District   
16   Downtown Toronto                                        Ryerson   
17         North York                                      Glencairn   
18          Etobicoke                                West Deane Park   
19          Etobicoke                               Princess Gardens   
20          Etobicoke                                   Martin Grove   
21          Etobicoke                                      Islington   
22          Etobicoke                                     Cloverdale   
23        Scarborough                                     Rouge Hill   
24        Scarborough                                     Port Union   
25        Scarborough                                 Highland Creek   
26         North York                                      Don Mills   
27          East York                               Woodbine Heights   
28   Downtown Toronto                                 St. James Town   
29               York                             Humewood-Cedarvale   
30          Etobicoke                                       Eringate   
31          Etobicoke                              Bloordale Gardens   
32          Etobicoke                              Old Burnhamthorpe   
33          Etobicoke                                  Markland Wood   
34        Scarborough                                      Guildwood   
35        Scarborough                                    Morningside   
36        Scarborough                                      West Hill   
37       East Toronto                                    The Beaches   
38   Downtown Toronto                                    Berczy Park   
39               York                            Caledonia-Fairbanks   
40        Scarborough                                         Woburn   
41          East York                                        Leaside   
42   Downtown Toronto                             Central Bay Street   
43   Downtown Toronto                                       Christie   
44        Scarborough                                      Cedarbrae   
45         North York                              Hillcrest Village   
46         North York                                 Bathurst Manor   
47         North York                                 Wilson Heights   
48         North York                                Downsview North   
49          East York                               Thorncliffe Park   
50   Downtown Toronto                                       Richmond   
51   Downtown Toronto                                       Adelaide   
52   Downtown Toronto                                           King   
53       West Toronto                                       Dufferin   
54       West Toronto                   

In [27]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighborhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park
Harbourfront
Lawrence Manor
Lawrence Heights
Queen's Park
Ontario Provincial Government
Islington Avenue
Humber Valley Village
Malvern
Rouge
Don Mills
Parkview Hill
Woodbine Gardens
Garden District
Ryerson
Glencairn
West Deane Park
Princess Gardens
Martin Grove
Islington
Cloverdale
Rouge Hill
Port Union
Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate
Bloordale Gardens
Old Burnhamthorpe
Markland Wood
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Wilson Heights
Downsview North
Thorncliffe Park
Richmond
Adelaide
King
Dufferin
Dovercourt Village
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Broadview North (Old East York)
Harbourfront East
Union Station
Toronto Islands
Little Portugal
Trinity
Kennedy Park
Ionview
East Birchmount Park
Bayview Village
Downsvi

### Lets see the size of the resulting Dataframe

In [28]:
print(toronto_venues.shape)
toronto_venues.head()

(5213, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods              43.758895              -79.320322   
1    Parkwoods              43.758895              -79.320322   
2    Parkwoods              43.758895              -79.320322   
3    Parkwoods              43.758895              -79.320322   
4    Parkwoods              43.758895              -79.320322   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0     Allwyn's Bakery       43.759840       -79.324719  Caribbean Restaurant  
1  Shoppers Drug Mart       43.760857       -79.324961              Pharmacy  
2         Food Basics       43.760549       -79.326045           Supermarket  
3        Petro-Canada       43.757950       -79.315187           Gas Station  
4         Pizza Pizza       43.760231       -79.325666           Pizza Place

Lets check how many venues were returned for each neighbourhood

In [29]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                           
Adelaide                                                          37   
Agincourt                                                         17   
Agincourt North                                                   28   
Albion Gardens                                                     4   
Alderwood                                                          5   
Bathurst Manor                                                     4   
Bathurst Quay                                                     26   
Bayview Village                                                    3   
Beaumond Heights                                                   4   
Bedford Park                                                       5   
Berczy Park                                                      100   
Birch Cliff                                                        4   
Bloordale Gardens                                                  4   
Broadview North (Old East York)                                    7   
Brockton                                                          44   
Business reply mail Processing Centre                            100   
CN Tower                                                          63   
Cabbagetown                                                       58   
Caledonia-Fairbanks                                                2   
Canada Post Gateway Processing Centre                             18   
Cedarbrae                                                          4   
Central Bay Street                                                41   
Chinatown                                                        100   
Christie                                                          16   
Church and Wellesley                                              73   
Clairlea                                                           5   
Clarks Corners                                                     9   
Cliffcrest                                                        10   
Cliffside                                                          8   
Cliffside West                                                     8   
Cloverdale                                                        22   
Commerce Court                                                   100   
Davisville                                                        15   
Davisville North                                                  15   
Deer Park                                                         26   
Del Ray                                                            6   
Design Exchange                                                  100   
Don Mills                                                          8   
Dorset Park                                                       11   
Dovercourt Village                                                66   
Downsview                                                         24   
Downsview North                                                    6   
Dufferin                                                           7   
East Birchmount Park                                              12   
East Toronto                                                      56   
Emery                                                              3   
Eringate                                                           5   
Exhibition Place                                                  33   
Fairview                                                          63   
First Canadian Place                                             100   
Forest Hill North & West                                           5   
Forest Hill Road Park                                              4   
Forest Hill SE                                                     5   
Garden District                                                  100   
Glencairn      

Lets find out how many unique categories there are

In [30]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 314 uniques categories.


## 4. Analyze each neighborhood

In [31]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Zoo  Accessories Store  Adult Boutique  Afghan Restaurant  Airport  \
0    0                  0               0                  0        0   
1    0                  0               0                  0        0   
2    0                  0               0                  0        0   
3    0                  0               0                  0        0   
4    0                  0               0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  Aquarium  \
0                    0             0               0             0         0   
1                    0             0               0             0         0   
2                    0             0               0             0         0   
3                    0             0               0             0         0   
4                    0             0               0             0         0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0               0                 0                   0      0   
1               0                 0                   0      0   
2               0                 0                   0      0   
3               0                 0                   0      0   
4               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0       0              0          0         0                     0   
1       0              0          0         0                     0   
2       0              0          0         0                     0   
3       0              0          0         0                     0  

Lets examine dataframe size

In [32]:
toronto_onehot.shape

(5213, 314)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [33]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood    Zoo  Accessories Store  \
0                                         Adelaide  0.000           0.000000   
1                                        Agincourt  0.000           0.000000   
2                                  Agincourt North  0.000           0.000000   
3                                   Albion Gardens  0.000           0.000000   
4                                        Alderwood  0.000           0.000000   
5                                   Bathurst Manor  0.000           0.000000   
6                                    Bathurst Quay  0.000           0.000000   
7                                  Bayview Village  0.000           0.000000   
8                                 Beaumond Heights  0.000           0.000000   
9                                     Bedford Park  0.000           0.000000   
10                                     Berczy Park  0.000           0.000000   
11                                     Birch Cliff  0.000           0.000000   
12                               Bloordale Gardens  0.000           0.000000   
13                 Broadview North (Old East York)  0.000           0.000000   
14                                        Brockton  0.000           0.000000   
15           Business reply mail Processing Centre  0.000           0.000000   
16                                        CN Tower  0.000           0.000000   
17                                     Cabbagetown  0.000           0.000000   
18                             Caledonia-Fairbanks  0.000           0.000000   
19           Canada Post Gateway Processing Centre  0.000           0.055556   
20                                       Cedarbrae  0.000           0.000000   
21                              Central Bay Street  0.000           0.000000   
22                                       Chinatown  0.000           0.000000   
23                                        Christie  0.000           0.000000   
24                            Church and Wellesley  0.000           0.000000   
25                                        Clairlea  0.000           0.000000   
26                                  Clarks Corners  0.000           0.000000   
27                                      Cliffcrest  0.000           0.000000   
28                                       Cliffside  0.000           0.000000   
29                                  Cliffside West  0.000           0.000000   
30                                      Cloverdale  0.000           0.000000   
31                                  Commerce Court  0.000           0.000000   
32                                      Davisville  0.000           0.000000   
33                                Davisville North  0.000           0.000000   
34                                       Deer Park  0.000           0.000000   
35                                         Del Ray  0.000           0.000000   
36                                 Design Exchange  0.000           0.000000   
37                                       Don Mills  0.000           0.000000   
38                                     Dorset Park  0.000           0.000000   
39                              Dovercourt Village  0.000           0.000000   
40                                       Downsview  0.000           0.000000   
41                                 Downsview North  0.000           0.000000   
42                                        Dufferin  0.000           0.000000   
43                            East Birchmount Park  0.000           0.000000   
44                                    East Toronto  0.000           0.000000   
45                                           Emery  0.000           0.000000   
46                                        Eringate  0.000           0.000000   
47                                Exhibition Place  0.000           0.000000   
48                                        Fairview  0.000           0.015873   
49                            First Ca

In [34]:
toronto_grouped.shape

(203, 314)

Let's print each neighborhood along with the top 5 most common venues

In [35]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
                venue  freq
0         Coffee Shop  0.16
1      Breakfast Spot  0.05
2              Bakery  0.05
3             Theater  0.05
4  Italian Restaurant  0.05


----Agincourt----
                   venue  freq
0     Chinese Restaurant  0.29
1       Asian Restaurant  0.18
2          Shopping Mall  0.12
3  Vietnamese Restaurant  0.06
4                Butcher  0.06


----Agincourt North----
                 venue  freq
0   Chinese Restaurant  0.07
1                 Bank  0.07
2               Bakery  0.07
3  Sporting Goods Shop  0.04
4           Restaurant  0.04


----Albion Gardens----
              venue  freq
0          Gym Pool  0.25
1      Hockey Arena  0.25
2  Sushi Restaurant  0.25
3    Hardware Store  0.25
4               Zoo  0.00


----Alderwood----
               venue  freq
0  Convenience Store   0.2
1        Pizza Place   0.2
2             Market   0.2
3       Burger Joint   0.2
4        Coffee Shop   0.2


----Bathurst Manor----
               venue 

4            Fried Chicken Joint  0.04


----Grange Park----
                venue  freq
0  Chinese Restaurant  0.09
1                Café  0.08
2         Coffee Shop  0.07
3         Art Gallery  0.04
4   Korean Restaurant  0.03


----Guildwood----
               venue  freq
0              Hotel   0.5
1               Park   0.5
2  Outdoor Sculpture   0.0
3    Organic Grocery   0.0
4       Optical Shop   0.0


----Harbord----
                venue  freq
0                Café  0.07
1         Coffee Shop  0.05
2    Sushi Restaurant  0.04
3      Sandwich Place  0.04
4  Italian Restaurant  0.03


----Harbourfront----
         venue  freq
0  Coffee Shop  0.09
1     Aquarium  0.05
2  Pizza Place  0.04
3        Hotel  0.03
4         Café  0.03


----Harbourfront East----
                venue  freq
0         Coffee Shop  0.11
1               Hotel  0.05
2    Asian Restaurant  0.03
3  Italian Restaurant  0.03
4                Café  0.03


----Harbourfront West----
                venue  freq
0 

                   venue  freq
0            Yoga Studio  0.25
1  Performing Arts Venue  0.25
2                 Bakery  0.25
3                    Bar  0.25
4   Other Great Outdoors  0.00


----Mimico NW----
                   venue  freq
0            Yoga Studio  0.25
1  Performing Arts Venue  0.25
2                 Bakery  0.25
3                    Bar  0.25
4   Other Great Outdoors  0.00


----Mimico South----
               venue  freq
0  Convenience Store  0.12
1      Grocery Store  0.12
2  Indian Restaurant  0.12
3     Breakfast Spot  0.06
4               Café  0.06


----Montgomery Road----
                venue  freq
0  Italian Restaurant  0.33
1    Tapas Restaurant  0.11
2       Grocery Store  0.11
3                Bank  0.11
4            Pharmacy  0.11


----Moore Park----
           venue  freq
0       Tea Room  0.12
1     Food Court  0.12
2  Grocery Store  0.12
3           Café  0.12
4           Park  0.12


----Morningside----
                  venue  freq
0           Coffee

4   Men's Store  0.04


----South Steeles----
           venue  freq
0    Gas Station  0.25
1  Moving Target  0.25
2  Jewelry Store  0.25
3    Video Store  0.25
4            Zoo  0.00


----South of Bloor----
            venue  freq
0          Bakery  0.09
1            Bank  0.09
2             Pub  0.09
3  Breakfast Spot  0.09
4    Liquor Store  0.09


----St. James Town----
                 venue  freq
0          Coffee Shop  0.15
1        Grocery Store  0.08
2             Pharmacy  0.04
3       Breakfast Spot  0.04
4  Filipino Restaurant  0.04


----St. Phillips----
                venue  freq
0         Golf Course   0.2
1         Pizza Place   0.2
2        Intersection   0.2
3         Coffee Shop   0.2
4  Golf Driving Range   0.2


----Steeles East----
                 venue  freq
0   Chinese Restaurant  0.14
1               Bakery  0.08
2      Bubble Tea Shop  0.06
3                 Bank  0.06
4  Japanese Restaurant  0.06


----Steeles West----
                 venue  freq
0   Chin

Let's put that into a pandas dataframe

In [39]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood  \
0                                         Adelaide   
1                                        Agincourt   
2                                  Agincourt North   
3                                   Albion Gardens   
4                                        Alderwood   
5                                   Bathurst Manor   
6                                    Bathurst Quay   
7                                  Bayview Village   
8                                 Beaumond Heights   
9                                     Bedford Park   
10                                     Berczy Park   
11                                     Birch Cliff   
12                               Bloordale Gardens   
13                 Broadview North (Old East York)   
14                                        Brockton   
15           Business reply mail Processing Centre   
16                                        CN Tower   
17                                     Cabbagetown   
18                             Caledonia-Fairbanks   
19           Canada Post Gateway Processing Centre   
20                                       Cedarbrae   
21                              Central Bay Street   
22                                       Chinatown   
23                                        Christie   
24                            Church and Wellesley   
25                                        Clairlea   
26                                  Clarks Corners   
27                                      Cliffcrest   
28                                       Cliffside   
29                                  Cliffside West   
30                                      Cloverdale   
31                                  Commerce Court   
32                                      Davisville   
33                                Davisville North   
34                                       Deer Park   
35                                         Del Ray   
36                                 Design Exchange   
37                                       Don Mills   
38                                     Dorset Park   
39                              Dovercourt Village   
40                                       Downsview   
41                                 Downsview North   
42                                        Dufferin   
43                            East Birchmount Park   
44                                    East Toronto   
45                                           Emery   
46                                        Eringate   
47                                Exhibition Place   
48                                        Fairview   
49                            First Canadian Place   
50                        Forest Hill North & West   
51                           Forest Hill Road Park   
52                                  Forest Hill SE   
53                                 Garden District   
54                                       Glencairn   
55                                     Golden Mile   
56                                     Grange Park   
57                                       Guildwood   
58                                         Harbord   
59                                    Harbourfront   
60                               Harbourfront East   
61                               Harbourfront West   
62                                      Henry Farm   
63                                       High Park   
64                                  Highland Creek   
65                               Hillcrest Village   
66                                      Humber Bay   
67                               Humber Bay Shores   
68                                   Humber Summit   
69                           Humber Valley Village   
70                                      Humbergate   
71                                       Humberlea   
72                              Humewood-Cedarvale   
73                                    Indi

## 5. Cluster Neighborhoods

Run k-means to cluster the neighborhood into 5 clusters.

In [51]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 0, 0, 2, 1, 2, 0, 1, 0], dtype=int32)

In [52]:
kmeans.labels_

array([2, 2, 0, 0, 2, 1, 2, 0, 1, 0, 2, 1, 0, 0, 2, 2, 2, 2, 1, 2, 1, 2,
       2, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 2, 0, 0, 2, 0,
       0, 2, 2, 2, 2, 2, 0, 1, 0, 2, 0, 0, 2, 1, 2, 2, 2, 2, 0, 0, 0, 1,
       2, 0, 0, 1, 1, 2, 0, 0, 4, 2, 0, 0, 0, 2, 2, 2, 2, 2, 1, 2, 1, 1,
       2, 2, 4, 0, 2, 2, 0, 2, 2, 0, 0, 4, 2, 3, 0, 0, 0, 0, 0, 2, 2, 2,
       2, 0, 2, 4, 2, 2, 2, 2, 0, 0, 2, 1, 1, 2, 2, 2, 2, 0, 1, 0, 2, 2,
       2, 2, 2, 1, 0, 2, 2, 0, 0, 0, 0, 2, 2, 2, 2, 2, 0, 2, 2, 0, 0, 2,
       2, 2, 0, 0, 2, 2, 2, 0, 0, 0, 0, 2, 2, 0, 0, 0, 2, 0, 2, 0, 0, 0,
       0, 2, 0, 2, 2, 2, 2, 0, 0, 2, 4, 0, 1, 2, 0, 2, 0, 1, 0, 1, 2, 0,
       0, 4, 4, 2, 2], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.b

In [53]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.merge(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged# check the last columns!

Borough                                   Neighborhood  \
0          North York                                      Parkwoods   
1          North York                               Victoria Village   
2    Downtown Toronto                                    Regent Park   
3    Downtown Toronto                                   Harbourfront   
4          North York                                 Lawrence Manor   
5          North York                               Lawrence Heights   
6    Downtown Toronto                                   Queen's Park   
7    Downtown Toronto                  Ontario Provincial Government   
8           Etobicoke                               Islington Avenue   
9           Etobicoke                          Humber Valley Village   
10        Scarborough                                        Malvern   
11        Scarborough                                          Rouge   
12         North York                                      Don Mills   
13         North York                                      Don Mills   
14          East York                               Woodbine Gardens   
15   Downtown Toronto                                Garden District   
16   Downtown Toronto                                        Ryerson   
17         North York                                      Glencairn   
18          Etobicoke                                West Deane Park   
19          Etobicoke                               Princess Gardens   
20          Etobicoke                                   Martin Grove   
21          Etobicoke                                      Islington   
22          Etobicoke                                     Cloverdale   
23        Scarborough                                     Port Union   
24        Scarborough                                 Highland Creek   
25   Downtown Toronto                                 St. James Town   
26   Downtown Toronto                                 St. James Town   
27               York                             Humewood-Cedarvale   
28          Etobicoke                                       Eringate   
29          Etobicoke                              Bloordale Gardens   
30          Etobicoke                              Old Burnhamthorpe   
31          Etobicoke                                  Markland Wood   
32        Scarborough                                      Guildwood   
33        Scarborough                                    Morningside   
34        Scarborough                                      West Hill   
35       East Toronto                                    The Beaches   
36   Downtown Toronto                                    Berczy Park   
37               York                            Caledonia-Fairbanks   
38        Scarborough                                         Woburn   
39          East York                                        Leaside   
40   Downtown Toronto                             Central Bay Street   
41   Downtown Toronto                                       Christie   
42        Scarborough                                      Cedarbrae   
43         North York                              Hillcrest Village   
44         North York                                 Bathurst Manor   
45         North York                                 Wilson Heights   
46         North York                                Downsview North   
47          East York                               Thorncliffe Park   
48   Downtown Toronto                                       Richmond   
49   Downtown Toronto                                       Adelaide   
50   Downtown Toronto                                           King   
51       West Toronto                                       Dufferin   
52       West Toronto                             Dovercourt Village   
53        Scarborough                            Scarborough Village   
54         North York                                 

In [54]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 6 Examine Clusters

### Cluster 1

In [55]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood       1st Most Common Venue  \
0                          Parkwoods           Convenience Store   
4                     Lawrence Manor                  Bagel Shop   
8                   Islington Avenue                 Yoga Studio   
10                           Malvern        Fast Food Restaurant   
11                             Rouge                 Gas Station   
14                  Woodbine Gardens          Mexican Restaurant   
17                         Glencairn            Asian Restaurant   
18                   West Deane Park                       Hotel   
19                  Princess Gardens                 Golf Course   
21                         Islington                 Yoga Studio   
24                    Highland Creek                 IT Services   
27                Humewood-Cedarvale           Convenience Store   
29                 Bloordale Gardens                        Bank   
35                       The Beaches                         Bar   
38                            Woburn           Indian Restaurant   
39                           Leaside              Sandwich Place   
46                   Downsview North                        Café   
47                  Thorncliffe Park                        Bank   
55                        Henry Farm                       Hotel   
57                    Northwood Park                    Tea Room   
59                      East Toronto               Grocery Store   
60   Broadview North (Old East York)              Sandwich Place   
63                   Toronto Islands                 Pizza Place   
68              East Birchmount Park                 Pizza Place   
69                   Bayview Village          Golf Driving Range   
70                         Downsview                        Café   
71                         Downsview                        Café   
72                         Downsview                        Café   
73                         Downsview                        Café   
74                 The Danforth West                 Coffee Shop   
75                         Riverdale             Thai Restaurant   
81                       Golden Mile          Chinese Restaurant   
82                          Clairlea                Soccer Field   
83                          Oakridge                     Dog Run   
85                      India Bazaar           Indian Restaurant   
86                  The Beaches West                         Bar   
90                   Maple Leaf Park  Construction & Landscaping   
91                       Upwood Park           Convenience Store   
92                     Humber Summit                   BBQ Joint   
98                      Bedford Park                   Bookstore   
107                  Willowdale East                 Wings Joint   
110                         Roselawn               Grocery Store   
120         Forest Hill North & West                        Park   
122                        High Park                         Zoo   
123               The Junction South                  Restaurant   
124                        Westmount           Convenience Store   
125                          Wexford   Middle Eastern Restaurant   
126                         Maryvale                        Pool   
143                          Swansea        Gym / Fitness Center   
148                  Summerhill East                        Park   
152                         Milliken          Chinese Restaurant   
153                  Agincourt North                        Bank   
154                     Steeles East          Chinese Restaurant   
156                  Summerhill West                        Park   
159                   Forest Hill SE           Convenience Store   
166                    South Niagara                 Yoga Studio   
169                     Mimico South               Grocery Store   
170                Humber Bay Shores                       Beach   
171         

### Cluster 2 

In [56]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood                     1st Most Common Venue  \
9       Humber Valley Village                                      Pool   
12                  Don Mills                             Hot Dog Joint   
13                  Don Mills                             Hot Dog Joint   
23                 Port Union                             Train Station   
32                  Guildwood                                     Hotel   
34                  West Hill                Construction & Landscaping   
37        Caledonia-Fairbanks                             Women's Store   
42                  Cedarbrae                                      Park   
43          Hillcrest Village  Residential Building (Apartment / Condo)   
44             Bathurst Manor                         Convenience Store   
105               Birch Cliff                                Playground   
116           Wexford Heights                             Deli / Bodega   
121     Forest Hill Road Park                              Skating Rink   
127           Willowdale West                         Mobile Phone Shop   
138          Richview Gardens                              Food Service   
173                Humbergate                                Playground   
176          Beaumond Heights                                      Park   
193            Old Mill North                                      Park   
197            Old Mill South                                      Park   
198          King's Mill Park                                      Park   
204  Kingsway Park South East                                      Park   
208  Kingsway Park South West                                      Park   

    2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
9         Harbor / Marina  Construction & Landscaping                  Park   
12      Convenience Store                Liquor Store                  Park   
13      Convenience Store                Liquor Store                  Park   
23               Bus Line                        Park           Yoga Studio   
32                   Park                     Dog Run            Donut Shop   
34                   Park                  Restaurant     Convenience Store   
37                   Park                     Dog Run            Donut Shop   
42             Playground               Grocery Store           Yoga Studio   
43                   Park             Doctor's Office      Doner Restaurant   
44             Playground                        Park        Baseball Field   
105              Pharmacy                        Café                  Park   
116                  Park            Doner Restaurant   Dumpling Restaurant   
121                  Park        Gym / Fitness Center           Yoga Studio   
127                  Park                     Dog Run            Donut Shop   
138         Moving Target                        Park          Intersection   
173                  Park        Gym / Fitness Center           Yoga Studio   
176          Skating Rink                      Bakery           Yoga Studio   
193   American Restaurant                         Spa         Metro Station   
197   American Restaurant                         Spa         Metro Station   
198                   Spa         American Restaurant                 River   
204            Kids Store                       River           Yoga Studio   
208            Kids Store                       River           Yoga Studio   

           5th Most Common Venue        6th Most Common Venue  \
9                     Donut Shop          Dumpling Restaurant   
12                       Exhibit          Dumpling Restaurant   
13                       Exhibit          Dumpling Restaurant   
23          Ethiopian Restaurant                   Donut Shop   
32           Dumpling Restaurant  Eastern European Restaurant   
34                      Tea Room                  Yoga Studio   
37           Dumpl

### Cluster 3

In [57]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  1st Most Common Venue  \
2                                      Regent Park            Coffee Shop   
3                                     Harbourfront            Coffee Shop   
6                                     Queen's Park            Coffee Shop   
7                    Ontario Provincial Government            Coffee Shop   
15                                 Garden District            Coffee Shop   
16                                         Ryerson                    Bar   
20                                    Martin Grove         Discount Store   
22                                      Cloverdale            Supermarket   
25                                  St. James Town            Coffee Shop   
26                                  St. James Town            Coffee Shop   
28                                        Eringate      Convenience Store   
30                               Old Burnhamthorpe                   Café   
33                                     Morningside            Coffee Shop   
36                                     Berczy Park            Coffee Shop   
40                              Central Bay Street       Sushi Restaurant   
41                                        Christie                   Park   
45                                  Wilson Heights            Coffee Shop   
48                                        Richmond            Coffee Shop   
49                                        Adelaide            Coffee Shop   
50                                            King            Coffee Shop   
51                                        Dufferin                 Bakery   
52                              Dovercourt Village                    Bar   
53                             Scarborough Village                Theater   
54                                        Fairview         Clothing Store   
56                                          Oriole            Pizza Place   
58                                 York University            Coffee Shop   
61                               Harbourfront East            Coffee Shop   
62                                   Union Station            Coffee Shop   
64                                 Little Portugal                    Bar   
65                                         Trinity            Men's Store   
66                                    Kennedy Park         Discount Store   
76                         Toronto Dominion Centre            Coffee Shop   
77                                 Design Exchange            Coffee Shop   
78                                        Brockton            Coffee Shop   
79                                Parkdale Village            Coffee Shop   
80                                Exhibition Place             Theme Park   
87                                  Commerce Court            Coffee Shop   
88                                  Victoria Hotel            Coffee Shop   
89                                      North Park              Pet Store   
93                                       Cliffside                  Hotel   
94                                      Cliffcrest         Ice Cream Shop   
95                        Scarborough Village West                Theater   
97                                 Studio District            Coffee Shop   
99                             Lawrence Manor East            Coffee Shop   
100                                        Del Ray            Pizza Place   
101                                   Mount Dennis            Pizza Place   
102                      Keelsdale and Silverthorn         Cosmetics Shop   
103                                      Humberlea            Pizza Place   
104                                          Emery         Clothing Store   
106                                 Cliffside West                  Hotel   
108                                  Lawrence Park            Coffee Shop   
109                               

### Cluster 4

In [58]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
137  Martin Grove Gardens                   Gym           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
137       Doctor's Office      Doner Restaurant            Donut Shop   

    6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
137   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   

    9th Most Common Venue 10th Most Common Venue  
137     Elementary School   Ethiopian Restaurant

### Cluster 5

In [49]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Empty DataFrame
Columns: [Neighborhood, 1st Most Common Venue, 2nd Most Common Venue, 3rd Most Common Venue, 4th Most Common Venue, 5th Most Common Venue, 6th Most Common Venue, 7th Most Common Venue, 8th Most Common Venue, 9th Most Common Venue, 10th Most Common Venue]
Index: []